In [1]:
import numpy as np
import pandas as pd
import plotly.express as px


In [2]:
df = pd.read_csv('../attack-sample-3m.csv')

/tmp/ipykernel_621062/2707439441.py:1: DtypeWarning: Columns (0,1,3,10,11,13,14,15,18,19,20,21,22,24,25,26,27,28,30,31,32,33,34,35,36,37,42,44,50,52,53,54,55,56,57,58,59,60,61,62,63,64,65,66,67,68,69,70,71,72) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('../attack-sample-3m.csv')


I will continue working on the tcp.flags and checking more hypothesis : SYN Flooding

I would like to focus on some features that are more relevant to anomalous activities. I will do data exploration, statistical analysis, and visualization for each of them. These features are:

1- tcp.flags  --> how can it be anomalous?
    - Unusual combinations of TCP flags (e.g., SYN and FIN together or ACK and RST together) can indicate port scanning, network mapping, or more sophisticated attacks like session hijacking.
    - SYN flooding, which sends a large number of SYN packets without completing the three-way handshake. packets with SYN flag set but no ACK flag set within a timeout period (possible SYN flooding
    - TCP reset, where a RST packet is sent pretending to be from the other end of an established connection. RST flag set but no ACK flag set (possible TCP reset)RST flag set but no matching connection state or sequence number (TCP reset prevention),

2- ip.ttl
3- frame.protocols
4- http.request.method
5- dns.flags.response and dns.flags.rcode
6- tcp.srcport and tcp.dstport
7- ip.flags and ip.frag_offset
8- tcp.window_size
9- http.request.uri and http.request.full_uri
10- alert

Hypothesis #2:
Unusual combinations of TCP flags can indicate port scanning, network mapping, or more sophisticated attacks like session hijacking.

 SYN is set but ACK is not --> Potential SYN Flooding attack
    - first I will need to create a filtered dataset containing only the packets with the unusual flag combinations

    - Then I will count occurrences over time or group by additional features like IP addresses or ports to see if there's a pattern or trend.Look at the IP addresses and ports involved with the unusual packets to see if they're coming from or going to known entities or a wide range of targets.


    - Visualise:
        - Time Series Plot: Show the count of unusual flag combinations over time.
        - Heatmap: If analyzing specific source/destination IPs or ports, a heatmap can show where the most activity is occurring.

    - Deep dive into specific events or patterns. Case Studies: I will pick out specific instances or bursts of unusual activity and investigate them in detail. I will look at the surrounding packets and what was happening on the network at that time.Correlation with Events: See if the spikes in unusual activity correlate with known network events, outages, or previously identified incidents.

    - Findings: Document the occurrences, patterns, and any identified anomalies.Implications: Discuss what these findings might mean for network security. Are there specific actions or investigations that should follow?

    - Adjust Parameters: Based on your findings, you might want to redefine what's considered unusual or look at additional flag combinations.Iterate: Repeat the analysis with the new parameters or as new data becomes available.

ACK and RST together -->


In [3]:
# SYN(set) and ACK(not set) together -->
df['tcp.flags.syn'].value_counts()

tcp.flags.syn
0.0              2884003
1.0               104080
0                   7927
1                    258
tcp.flags.syn          1
Name: count, dtype: int64

In [4]:
df['tcp.flags.ack'].value_counts()


tcp.flags.ack
1.0              2901670
0.0                86413
1                   7970
0                    215
tcp.flags.ack          1
Name: count, dtype: int64

In [5]:
# I'm looking where SYN flags are present but ACK ones are missing. so I'll drop the NaN rows where SYN is not present.

df = df.dropna(subset=['tcp.flags.syn'])
df['tcp.flags.syn'].value_counts()

tcp.flags.syn
0.0              2884003
1.0               104080
0                   7927
1                    258
tcp.flags.syn          1
Name: count, dtype: int64

In [6]:
df = df[df['tcp.flags.syn'] != 'tcp.flags.syn']

In [7]:
df['tcp.flags.syn'].value_counts()

tcp.flags.syn
0.0    2884003
1.0     104080
0         7927
1          258
Name: count, dtype: int64

In [9]:
df_syn_ack = df[(df['tcp.flags.syn'] == 1.0) & ((df['tcp.flags.ack'] == 0) | (df['tcp.flags.ack'] == 0.0))]

In [10]:
df_syn_ack

frame.number frame.len                           frame.time  \
75             97219        74  Jun  4, 2023 11:25:35.416580000 EDT   
145          5895776        74  Jun  4, 2023 12:33:19.978076000 EDT   
273            55270        74  Jun  4, 2023 11:25:34.207886000 EDT   
276            34529        74  Jun  4, 2023 11:25:33.653935000 EDT   
295          5884906        74  Jun  4, 2023 12:33:19.657720000 EDT   
...              ...       ...                                  ...   
2999730       126165        74  Jun  4, 2023 11:25:36.190572000 EDT   
2999779      5823297        74  Jun  4, 2023 12:33:16.632099000 EDT   
2999868        87745        74  Jun  4, 2023 11:25:35.113556000 EDT   
2999944        32419        74  Jun  4, 2023 11:25:33.600643000 EDT   
2999976      5926965        74  Jun  4, 2023 12:33:20.917884000 EDT   

          frame.time_epoch       frame.protocols            eth.src  \
75        1685892335.41658  eth:ethertype:ip:tcp  00:0c:29:94:f6:85   
145      1685896399.978076  eth:ethertype:ip:tcp  00:0c:29:94:f6:85   
273      1685892334.207886  eth:ethertype:ip:tcp  00:0c:29:94:f6:85   
276      1685892333.653935  eth:ethertype:ip:tcp  00:0c:29:94:f6:85   
295       1685896399.65772  eth:ethertype:ip:tcp  00:0c:29:94:f6:85   
...                    ...                   ...                ...   
2999730  1685892336.190572  eth:ethertype:ip:tcp  00:0c:29:94:f6:85   
2999779  1685896396.632099  eth:ethertype:ip:tcp  00:0c:29:94:f6:85   
2999868  1685892335.113556  eth:ethertype:ip:tcp  00:0c:29:94:f6:85   
2999944  1685892333.600643  eth:ethertype:ip:tcp  00:0c:29:94:f6:85   
2999976  1685896400.917884  eth:ethertype:ip:tcp  00:0c:29:94:f6:85   

                   eth.dst eth.type        ip.src        ip.dst  ...  \
75       00:0c:29:8f:ca:0a   0x0800  10.20.30.103  10.20.30.101  ...   
145      00:0c:29:8f:ca:0a   0x0800  10.20.30.103  10.20.30.101  ...   
273      00:0c:29:8f:ca:0a   0x0800  10.20.30.103  10.20.30.101  ...   
276      00:0c:29:8f:ca:0a   0x0800  10.20.30.103  10.20.30.101  ...   
295      00:0c:29:8f:ca:0a   0x0800  10.20.30.103  10.20.30.101  ...   
...                    ...      ...           ...           ...  ...   
2999730  00:0c:29:8f:ca:0a   0x0800  10.20.30.103  10.20.30.101  ...   
2999779  00:0c:29:8f:ca:0a   0x0800  10.20.30.103  10.20.30.101  ...   
2999868  00:0c:29:8f:ca:0a   0x0800  10.20.30.103  10.20.30.101  ...   
2999944  00:0c:29:8f:ca:0a   0x0800  10.20.30.103  10.20.30.101  ...   
2999976  00:0c:29:8f:ca:0a   0x0800  10.20.30.103  10.20.30.101  ...   

        imap.request.command imap.response ftp.request.command  \
75                       NaN           NaN                 NaN   
145                      NaN           NaN                 NaN   
273                      NaN           NaN                 NaN   
276                      NaN           NaN                 NaN   
295                      NaN           NaN                 NaN   
...                      ...           ...                 ...   
2999730                  NaN           NaN                 NaN   
2999779                  NaN           NaN                 NaN   
2999868                  NaN           NaN                 NaN   
2999944                  NaN           NaN                 NaN   
2999976                  NaN           NaN                 NaN   

        ftp.request.arg ftp.response.code ftp.response.arg ipv6.src ipv6.dst  \
75                  NaN               NaN              NaN      NaN      NaN   
145                 NaN               NaN              NaN      NaN      NaN   
273                 NaN               NaN              NaN      NaN      NaN   
276                 NaN               NaN              NaN      NaN      NaN   
295                 NaN               NaN              NaN      NaN      NaN   
...                 ...               ...              ...      ...      ...   
2999730             NaN               NaN              NaN      NaN      NaN   
2999

There are 83972 rows.  I will try to see the timing of these packets. Are they spread out, or do they occur in bursts

In [11]:
df_syn_ack['datetime'] = pd.to_datetime(df_syn_ack['frame.time'])
df_syn_ack['datetime']

/media/sumanas/Storage/envs/lowl-jaja-test/lib/python3.10/site-packages/dateutil/parser/_parser.py:1207: UnknownTimezoneWarning: tzname EDT identified but not understood.  Pass `tzinfos` argument in order to correctly return a timezone-aware datetime.  In a future version, this will raise an exception.
  warnings.warn("tzname {tzname} identified but not understood.  "
/tmp/ipykernel_621062/3112829161.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_syn_ack['datetime'] = pd.to_datetime(df_syn_ack['frame.time'])


75        2023-06-04 11:25:35.416580
145       2023-06-04 12:33:19.978076
273       2023-06-04 11:25:34.207886
276       2023-06-04 11:25:33.653935
295       2023-06-04 12:33:19.657720
                     ...            
2999730   2023-06-04 11:25:36.190572
2999779   2023-06-04 12:33:16.632099
2999868   2023-06-04 11:25:35.113556
2999944   2023-06-04 11:25:33.600643
2999976   2023-06-04 12:33:20.917884
Name: datetime, Length: 83972, dtype: datetime64[ns]

I'm going to calculate time differences in seconds from the first packet.
By setting the first packet's arrival time as a baseline (zero point), I can create a relative time frame. This makes it easier to understand the distribution and frequency of events in relation to the start of the capture. It provides a clear, consistent point of reference for all subsequent data points.

In [12]:
first_time = df_syn_ack['datetime'].iloc[0]
first_time

Timestamp('2023-06-04 11:25:35.416580')

Calculate time differences in seconds from the first packet. In pandas, .dt is an accessor object for datetimelike properties of the Series values. When we have a Series of datetime objects in a pandas DataFrame, .dt allows us to access the values of the series as datetimelike and perform operations on them. The .total_seconds() method is one such methods which converts the duration represented by the timedelta object into the total number of seconds.

In [13]:
df_syn_ack['time_diff'] = (df_syn_ack['datetime'] - first_time).dt.total_seconds()
df_syn_ack['time_diff']

/tmp/ipykernel_621062/1933329428.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_syn_ack['time_diff'] = (df_syn_ack['datetime'] - first_time).dt.total_seconds()


75            0.000000
145        4064.561496
273          -1.208694
276          -1.762645
295        4064.241140
              ...     
2999730       0.773992
2999779    4061.215519
2999868      -0.303024
2999944      -1.815937
2999976    4065.501304
Name: time_diff, Length: 83972, dtype: float64

In [14]:
fig = px.scatter(df_syn_ack,
                 x='time_diff',
                 y=df_syn_ack.index,
                 title='Packet Occurrence Over Time',
                 labels={'x': 'Time from first packet (seconds)', 'y': 'Packet index'})

fig.show()

Vertical alignments of points --> this could suggest that multiple packets were transmitted at nearly the same time.

In [15]:
df_syn_ack.columns

Index(['frame.number', 'frame.len', 'frame.time', 'frame.time_epoch',
       'frame.protocols', 'eth.src', 'eth.dst', 'eth.type', 'ip.src', 'ip.dst',
       'ip.len', 'ip.ttl', 'ip.flags', 'ip.frag_offset', 'ip.proto',
       'ip.version', 'ip.dsfield', 'ip.checksum', 'tcp.srcport', 'tcp.dstport',
       'tcp.len', 'tcp.seq', 'tcp.ack', 'tcp.flags', 'tcp.flags.syn',
       'tcp.flags.ack', 'tcp.flags.fin', 'tcp.flags.reset', 'tcp.window_size',
       'tcp.checksum', 'tcp.stream', 'udp.srcport', 'udp.dstport',
       'udp.length', 'udp.checksum', 'icmp.type', 'icmp.code', 'icmp.checksum',
       'http.request.method', 'http.request.uri', 'http.request.version',
       'http.request.full_uri', 'http.response.code', 'http.user_agent',
       'http.content_length_header', 'http.content_type', 'http.cookie',
       'http.host', 'http.referer', 'http.location', 'http.authorization',
       'http.connection', 'dns.qry.name', 'dns.qry.type', 'dns.qry.class',
       'dns.flags.response', 'dns.f

I would like to count the number of packets that occurred in each time interval (every 10 second)

In [16]:
time_interval = 10

In [17]:
grouped = df_syn_ack.groupby(df_syn_ack['time_diff'] // time_interval).size()

grouped_df = grouped.reset_index(name='packet_count')

In [21]:
fig = px.bar(grouped_df,
             x='time_diff',
             y='packet_count',
             title='Number of Packets per Time Interval (10 Seconds)',
             labels={'time_diff': 'Time Interval', 'packet_count': 'Number of Packets'},
             color_discrete_sequence=['cyan'])

fig.update_layout({
    'plot_bgcolor': 'white',
    'paper_bgcolor': 'white',
    'font_color': 'black'})


fig.show()

I see a couple of spikes at time interval :1 , 0, 406